# This is the second of two Cleaning Notebooks and uses a csv output from the first notebook

In [1]:
# Dependencies
import pandas as pd
import os
import numpy as np
import requests
import json
from pprint import pprint
from config import yelp_key
from statistics import mean, median 

The first step is to bring in the csv file created from the crime data

In [2]:
#Bring in the csv file created from the Crime Data and convert to a dataframe
csvpath = os.path.join("Crime_data.csv")
crime_df = pd.read_csv(csvpath, encoding="UTF-8")
crime_df.head()

County  Crime Rate per 100k  Murder  Rape  Robbery  Assault  \
0     St. Louis city, MO          1791.995377     119   200     1778     3609   
1  Crittenden County, AR          1754.914968       8    38      165      662   
2   Alexander County, IL          1664.700485       1     2        5      119   
3      Kenedy County, TX          1456.310680       0     3        1        2   
4     De Soto Parish, LA          1447.402430       3     4       17      368   

   Burglary  Larceny  MV Theft  Arson  Population  
0      4995    13791      3543    464      318416  
1      1482     1753       189     28       49746  
2        82      184        12      2        7629  
3         5        4         4      0         412  
4       149      494        60      0       27083

Next we create some additional columns to store the data we grab from the Yelp Reviews

In [7]:
#Creating empty columns in the dataframe to capture our new data
crime_df["Avg_Rating"] = ""
crime_df["Median_Rating"]=""
crime_df["Avg_Price"]=""
crime_df["Rest_Count"]=""
crime_df["Avg_Lat"]=""
crime_df["Avg_Lng"] =""

#View the first 5 rows of the dataframe
len(crime_df)
crime_df.head()

County  Crime Rate per 100k  Murder  Rape  Robbery  Assault  \
0     St. Louis city, MO          1791.995377     119   200     1778     3609   
1  Crittenden County, AR          1754.914968       8    38      165      662   
2   Alexander County, IL          1664.700485       1     2        5      119   
3      Kenedy County, TX          1456.310680       0     3        1        2   
4     De Soto Parish, LA          1447.402430       3     4       17      368   

   Burglary  Larceny  MV Theft  Arson  Population Avg_Rating Median_Rating  \
0      4995    13791      3543    464      318416                            
1      1482     1753       189     28       49746                            
2        82      184        12      2        7629                            
3         5        4         4      0         412                            
4       149      494        60      0       27083                            

  Avg_Price Rest_Count Avg_Lat Avg_Lng  
0                                       
1                                       
2                                       
3                                       
4

Next, we set up the Yelp API call and pulled some sample data to view the structure.

In [4]:
# Set up the url and headers for the YELP API call
headers = { 'Authorization': 'Bearer {}'.format(yelp_key),}
base_url = "https://api.yelp.com/v3/businesses/search"

#View the output of a sample call of the json to view the formatting
response = requests.get(base_url, params = {"location":"Mercer, NJ", "Catergories":"Restaurants", "limit": 5}, headers = headers)
json_data = response.json()
pprint (json_data)

{'businesses': [{'alias': 'grounds-for-sculpture-hamilton',
                 'categories': [{'alias': 'museums', 'title': 'Museums'},
                                {'alias': 'venues',
                                 'title': 'Venues & Event Spaces'}],
                 'coordinates': {'latitude': 40.236509,
                                 'longitude': -74.720399},
                 'display_phone': '(609) 586-0616',
                 'distance': 4749.23970857793,
                 'id': 'vV57YWbrHqm1iylWmIdwVA',
                 'image_url': 'https://s3-media3.fl.yelpcdn.com/bphoto/l7V3xHvu3HfysXlRDeB6Bg/o.jpg',
                 'is_closed': False,
                 'location': {'address1': '80 Sculptors Way',
                              'address2': '',
                              'address3': '',
                              'city': 'Hamilton',
                              'country': 'US',
                              'display_address': ['80 Sculptors Way',
                      

The next task was to loop through each of the countries and pull the json data. From that we had to loop through the up to 50 restaurants listed and grab the average rating, median rating, average price, number of restaurants, and their average latitute and longitude (so we can map them later on.)

In [9]:
# For each county run through the restaurants
for county_num in range(0, len(crime_df)):
    # Call the url
    response = requests.get(base_url, params = {"location":crime_df["County"][county_num], "Catergories":"Restaurants", "limit": 50}, headers = headers)
    # Convert to json
    json_data = response.json()
    # empty lists for data
    ratings = []
    price = []
    lat = []
    lng = []
    i=0
    # Run through the 50 rows of data and append the data to the empty lists
    # Exceptions were created to handle when their is no item listed or less than 50 restaurants
    for row in range (0, 50):
        try:
            ratings.append(json_data["businesses"][row]["rating"])
            i += 1
        except (KeyError, IndexError):
            print(str(country_num) + " of " + str(len(crime_df)) + " No rating for " + crime_df["County"][county_num] + " " + str(i))
        try:
            price.append(len(json_data["businesses"][row]["price"]))
        except (KeyError, IndexError):
            print (str(country_num) + " of " + str(len(crime_df)) + " No price for " + crime_df["County"][county_num] + " " + str(i))    
        try:
            lat.append(json_data["businesses"][row]["coordinates"]["latitude"])
        except (KeyError, IndexError):
            print (str(country_num) + " of " + str(len(crime_df)) + " No Lat for " + crime_df["County"][county_num] + " " + str(i))    
        try:
            lng.append(json_data["businesses"][row]["coordinates"]["longitude"])
        except (KeyError, IndexError):
            print (str(country_num) + " of " + str(len(crime_df)) + " No Lng for " + crime_df["County"][county_num] + " " + str(i))    
    # Use index of the country to place the averages (or medians) of each value into the dataframe
    # Exception created to handle when there isn't any restaurants or items to preform the task
    # Used .at to modify the dataframe itself and not a copy
    try:
        crime_df.at[county_num, "Rest_Count"]= i
        crime_df.at[county_num, "Avg_Rating"] = (mean(ratings))
        crime_df.at[county_num, "Median_Rating"] = (median(ratings))
        crime_df.at[county_num, "Avg_Price"] =  (mean(price))
        crime_df.at[county_num, "Avg_Lat"] = (mean(lat))
        crime_df.at[county_num, "Avg_Lng"]= (mean(lng))

    except:
        crime_df.at[county_num, "Rest_Count"]= 0
        crime_df.at[county_num,"Avg_Rating"] = 0
        crime_df.at[county_num,"Median_Rating"] = 0
        crime_df.at[county_num,"Avg_Price"] =  0
        crime_df.at[county_num,"Avg_Lat"] = 0
        crime_df.at[county_num,"Avg_Lng"]= 0
# View a sample of the new data
crime_df.head()

No price for St. Louis city, MO 3
No price for St. Louis city, MO 10
No price for St. Louis city, MO 22
No price for St. Louis city, MO 30
No price for St. Louis city, MO 36
No price for Crittenden County, AR 7
No price for Crittenden County, AR 22
No price for Crittenden County, AR 25
No price for Crittenden County, AR 26
No price for Crittenden County, AR 35
No price for Crittenden County, AR 38
No price for Crittenden County, AR 39
No price for Crittenden County, AR 46
No price for Kenedy County, TX 1
No price for Kenedy County, TX 4
No price for Kenedy County, TX 5
No rating for Kenedy County, TX 8
No price for Kenedy County, TX 8
No Lat for Kenedy County, TX 8
No Lng for Kenedy County, TX 8
No rating for Kenedy County, TX 8
No price for Kenedy County, TX 8
No Lat for Kenedy County, TX 8
No Lng for Kenedy County, TX 8
No rating for Kenedy County, TX 8
No price for Kenedy County, TX 8
No Lat for Kenedy County, TX 8
No Lng for Kenedy County, TX 8
No rating for Kenedy County, TX 8
No 

No price for Baltimore city, MD 27
No price for Baltimore city, MD 35
No price for Baltimore city, MD 36
No price for Shelby County, TN 5
No price for Shelby County, TN 6
No price for Shelby County, TN 8
No price for Shelby County, TN 42
No price for Marlboro County, SC 8
No price for Marlboro County, SC 10
No price for Marlboro County, SC 11
No price for Marlboro County, SC 12
No price for Marlboro County, SC 18
No price for Marlboro County, SC 19
No price for Marlboro County, SC 23
No rating for Marlboro County, SC 25
No price for Marlboro County, SC 25
No Lat for Marlboro County, SC 25
No Lng for Marlboro County, SC 25
No rating for Marlboro County, SC 25
No price for Marlboro County, SC 25
No Lat for Marlboro County, SC 25
No Lng for Marlboro County, SC 25
No rating for Marlboro County, SC 25
No price for Marlboro County, SC 25
No Lat for Marlboro County, SC 25
No Lng for Marlboro County, SC 25
No rating for Marlboro County, SC 25
No price for Marlboro County, SC 25
No Lat for Marl

No price for Philadelphia County, PA 15
No price for Philadelphia County, PA 19
No price for Pershing County, NV 8
No price for Pershing County, NV 14
No price for Pershing County, NV 34
No price for Pershing County, NV 36
No price for Pershing County, NV 37
No price for Pershing County, NV 41
No price for Pershing County, NV 43
No price for Pershing County, NV 48
No price for Greenwood County, SC 12
No price for Greenwood County, SC 21
No price for Greenwood County, SC 26
No price for Greenwood County, SC 29
No price for Greenwood County, SC 40
No price for Greenwood County, SC 43
No price for Greenwood County, SC 46
No price for Madison County, TN 3
No price for Madison County, TN 43
No price for Madison County, TN 47
No price for Madison County, TN 49
No price for Madison County, TN 50
No price for Marion County, IN 16
No price for Marion County, IN 36
No price for Wayne County, MI 3
No price for Wayne County, MI 36
No price for Jackson County, MO 4
No price for Jackson County, MO 3

No price for Pemiscot County, MO 5
No price for Pemiscot County, MO 7
No price for Pemiscot County, MO 14
No price for Pemiscot County, MO 15
No rating for Pemiscot County, MO 16
No price for Pemiscot County, MO 16
No Lat for Pemiscot County, MO 16
No Lng for Pemiscot County, MO 16
No rating for Pemiscot County, MO 16
No price for Pemiscot County, MO 16
No Lat for Pemiscot County, MO 16
No Lng for Pemiscot County, MO 16
No rating for Pemiscot County, MO 16
No price for Pemiscot County, MO 16
No Lat for Pemiscot County, MO 16
No Lng for Pemiscot County, MO 16
No rating for Pemiscot County, MO 16
No price for Pemiscot County, MO 16
No Lat for Pemiscot County, MO 16
No Lng for Pemiscot County, MO 16
No rating for Pemiscot County, MO 16
No price for Pemiscot County, MO 16
No Lat for Pemiscot County, MO 16
No Lng for Pemiscot County, MO 16
No rating for Pemiscot County, MO 16
No price for Pemiscot County, MO 16
No Lat for Pemiscot County, MO 16
No Lng for Pemiscot County, MO 16
No rating fo

No price for Muskogee County, OK 4
No price for Muskogee County, OK 6
No price for Muskogee County, OK 9
No price for Muskogee County, OK 11
No price for Muskogee County, OK 12
No price for Muskogee County, OK 13
No price for Muskogee County, OK 14
No rating for Muskogee County, OK 15
No price for Muskogee County, OK 15
No Lat for Muskogee County, OK 15
No Lng for Muskogee County, OK 15
No rating for Muskogee County, OK 15
No price for Muskogee County, OK 15
No Lat for Muskogee County, OK 15
No Lng for Muskogee County, OK 15
No rating for Muskogee County, OK 15
No price for Muskogee County, OK 15
No Lat for Muskogee County, OK 15
No Lng for Muskogee County, OK 15
No rating for Muskogee County, OK 15
No price for Muskogee County, OK 15
No Lat for Muskogee County, OK 15
No Lng for Muskogee County, OK 15
No rating for Muskogee County, OK 15
No price for Muskogee County, OK 15
No Lat for Muskogee County, OK 15
No Lng for Muskogee County, OK 15
No rating for Muskogee County, OK 15
No price 

...

No price for Benton County, IN 2
No price for Benton County, IN 4
No price for Benton County, IN 5
No price for Benton County, IN 6
No price for Benton County, IN 7
No price for Benton County, IN 8
No price for Benton County, IN 9
No price for Benton County, IN 10
No rating for Benton County, IN 10
No price for Benton County, IN 10
No Lat for Benton County, IN 10
No Lng for Benton County, IN 10
No rating for Benton County, IN 10
No price for Benton County, IN 10
No Lat for Benton County, IN 10
No Lng for Benton County, IN 10
No rating for Benton County, IN 10
No price for Benton County, IN 10
No Lat for Benton County, IN 10
No Lng for Benton County, IN 10
No rating for Benton County, IN 10
No price for Benton County, IN 10
No Lat for Benton County, IN 10
No Lng for Benton County, IN 10
No rating for Benton County, IN 10
No price for Benton County, IN 10
No Lat for Benton County, IN 10
No Lng for Benton County, IN 10
No rating for Benton County, IN 10
No price for Benton County, IN 10
N

No price for Cass County, MI 16
No price for Cass County, MI 17
No price for Cass County, MI 18
No price for Cass County, MI 19
No price for Cass County, MI 24
No price for Cass County, MI 32
No rating for Cass County, MI 33
No price for Cass County, MI 33
No Lat for Cass County, MI 33
No Lng for Cass County, MI 33
No rating for Cass County, MI 33
No price for Cass County, MI 33
No Lat for Cass County, MI 33
No Lng for Cass County, MI 33
No rating for Cass County, MI 33
No price for Cass County, MI 33
No Lat for Cass County, MI 33
No Lng for Cass County, MI 33
No rating for Cass County, MI 33
No price for Cass County, MI 33
No Lat for Cass County, MI 33
No Lng for Cass County, MI 33
No rating for Cass County, MI 33
No price for Cass County, MI 33
No Lat for Cass County, MI 33
No Lng for Cass County, MI 33
No rating for Cass County, MI 33
No price for Cass County, MI 33
No Lat for Cass County, MI 33
No Lng for Cass County, MI 33
No rating for Cass County, MI 33
No price for Cass County,

No price for Hale County, AL 2
No price for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7
No Lng for Hale County, AL 7
No rating for Hale County, AL 7
No price for Hale County, AL 7
No Lat for Hale County, AL 7

No price for Bollinger County, MO 11
No price for Bollinger County, MO 23
No price for Bollinger County, MO 25
No price for Bollinger County, MO 34
No price for Bollinger County, MO 35
No price for Bollinger County, MO 36
No price for Bollinger County, MO 38
No price for Bollinger County, MO 40
No price for Bollinger County, MO 44
No price for Bollinger County, MO 47
No price for Bollinger County, MO 49
No price for Bollinger County, MO 50
No price for Reeves County, TX 4
No price for Reeves County, TX 7
No price for Reeves County, TX 8
No price for Reeves County, TX 11
No price for Reeves County, TX 14
No price for Reeves County, TX 21
No price for Reeves County, TX 24
No price for Reeves County, TX 27
No price for Reeves County, TX 31
No rating for Reeves County, TX 31
No price for Reeves County, TX 31
No Lat for Reeves County, TX 31
No Lng for Reeves County, TX 31
No rating for Reeves County, TX 31
No price for Reeves County, TX 31
No Lat for Reeves County, TX 31
No Lng for Reeves C

SSLError: HTTPSConnectionPool(host='api.yelp.com', port=443): Max retries exceeded with url: /v3/businesses/search?location=Arlington+County%2C+VA&Catergories=Restaurants&limit=50 (Caused by SSLError(SSLError("bad handshake: SysCallError(54, 'ECONNRESET')")))

In [10]:
crime_df.head()

County  Crime Rate per 100k  Murder  Rape  Robbery  Assault  \
0     St. Louis city, MO          1791.995377     119   200     1778     3609   
1  Crittenden County, AR          1754.914968       8    38      165      662   
2   Alexander County, IL          1664.700485       1     2        5      119   
3      Kenedy County, TX          1456.310680       0     3        1        2   
4     De Soto Parish, LA          1447.402430       3     4       17      368   

   Burglary  Larceny  MV Theft  Arson  Population Avg_Rating Median_Rating  \
0      4995    13791      3543    464      318416       4.37           4.5   
1      1482     1753       189     28       49746       3.36           3.5   
2        82      184        12      2        7629       4.16             4   
3         5        4         4      0         412      3.625          3.75   
4       149      494        60      0       27083      3.875             4   

  Avg_Price Rest_Count  Avg_Lat  Avg_Lng  
0   1.97778         50   38.627 -90.2951  
1   1.35714         50  35.1699 -90.4249  
2      1.72         50  37.2581 -89.5209  
3       1.2          8  27.2326 -97.7406  
4   1.28571         16   32.065 -93.6993

Next, we seperated the dataframe into two sets: Those with and without restaurants

In [ ]:
# splitting the data
summary_df = crime_df.loc[crime_df["Rest_Count"] != 0, :]
zero_df = crime_df.loc[crime_df["Rest_Count"] == 0, :]

Finally, we pushed our dataframe out to a csv for further analysis.

In [ ]:
# Convert to csv
summary_df.to_csv("Yelp_data.csv", index=False, header=True)
zero_df.to_csv("zero_data.csv", index=False, header=True)